# VacationPy
---

## Starter Code to Import Libraries and Load the Weather and Coordinates Data

In [1]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key

In [2]:
# Load the CSV file created in Part 1 into a Pandas DataFrame
city_data_df = pd.read_csv("output_data/cities.csv")

# Display sample data
city_data_df.head()

City_ID          City      Lat       Lng  Max Temp  Humidity  Cloudiness  \
0        0      waitangi -43.9535 -176.5597     14.34        96          89   
1        1        bethel  41.3712  -73.4140      4.05        64          40   
2        2     adamstown -25.0660 -130.1015     23.34        65          79   
3        3  invercargill -46.4000  168.3500     11.68        93          91   
4        4        soller  39.7662    2.7152     17.14        62         100   

   Wind Speed Country        Date  
0        1.34      NZ  1711794322  
1        1.34      US  1711794323  
2       11.22      PN  1711794323  
3        0.89      NZ  1711794204  
4        5.76      ES  1711794323

---

### Step 1: Create a map that displays a point for every city in the `city_data_df` DataFrame. The size of the point should be the humidity in each city.

In [13]:
# Create a map plot with points for each city, where size represents humidity
map_plot = city_data_df.hvplot.scatter(x='Lng', y='Lat', size='Humidity', c='Humidity', by='City', 
                             geo=True, hover_cols=['City', 'Humidity'],
                             title='City Humidity Map', legend='right')
city_data_df.hvplot.scatter()

# Display the map plot
map_plot

:NdOverlay   [City]
   :Scatter   [Lng]   (Lat,Humidity,City)

In [3]:
%%capture --no-display

# Configure the map plot
# YOUR CODE HERE

# Display the map
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Humidity)

### Step 2: Narrow down the `city_data_df` DataFrame to find your ideal weather condition

In [58]:
# Narrow down cities that fit criteria and drop any results with null values
temp_filt = (city_data_df['Max Temp']>15) & (city_data_df['Max Temp']<30)
lat_filt = (city_data_df['Lat']>15) & (city_data_df['Lat']<50)
long_filt = (city_data_df['Lng']>-120) & (city_data_df['Lng']<-80)
hum_filt =(city_data_df['Humidity']>10) & (city_data_df['Humidity']<=100)
ideal_weather_df = city_data_df[temp_filt&lat_filt&hum_filt&long_filt]

# Drop any rows with null values
ideal_weather_df.dropna()

# Display sample data
ideal_weather_df


City_ID                    City      Lat       Lng  Max Temp  Humidity  \
83        83               champoton  19.3500  -90.7167     20.25        81   
130      130                   crane  31.3974 -102.3501     16.29        73   
184      184             isla aguada  18.7833  -91.4667     23.11        72   
195      195         lazaro cardenas  17.9583 -102.2000     20.74        62   
203      203                galliano  29.4422  -90.2992     17.00        82   
220      220      brisas de zicatela  15.8369  -97.0419     25.46        71   
234      234                celestun  20.8667  -90.4000     20.47        75   
251      251             sellersburg  38.3981  -85.7550     15.99        48   
253      253         dzilam gonzalez  21.2833  -88.9333     17.00        80   
257      257            san patricio  28.0170  -97.5169     21.02        85   
268      268                 cabanas  22.9758  -82.9219     19.64        71   
277      277          cabo san lucas  22.8909 -109.9124     18.75        91   
330      330                mazatlan  23.2167 -106.4167     18.28        83   
349      349           bahia de kino  28.8333 -111.9333     18.79        81   
434      434                robinson  31.4677  -97.1147     18.14        89   
523      523               ingleside  27.8778  -97.2117     21.10        88   
564      564                  panaba  21.2833  -88.2667     17.05        79   
565      565  tlahualilo de zaragoza  26.1167 -103.4500     18.59        14   

     Cloudiness  Wind Speed Country        Date  
83            1        4.50      MX  1711794338  
130          99        4.80      US  1711794346  
184          91        6.95      MX  1711794354  
195           0        1.52      MX  1711794357  
203           0        1.54      US  1711794359  
220           5        2.14      MX  1711794362  
234           0        5.73      MX  1711794364  
251          98        5.34      US  1711794276  
253           0        2.09      MX  1711794367  
257          14        6.06      US  1711794368  
268           0        3.63      CU  1711794369  
277          12        2.68      MX  1711794371  
330           0        0.45      MX  1711794284  
349         100        4.51      MX  1711794224  
434         100        7.20      US  1711794404  
523          40        5.14      US  1711794419  
564           0        3.09      MX  1711794425  
565          10        3.44      MX  1711794426

### Step 3: Create a new DataFrame called `hotel_df`.

In [59]:
# Use the Pandas copy function to create DataFrame called hotel_df to store the city, country, coordinates, and humidity
columns_to_copy = ['City', 'Country', 'Lat', 'Lng', 'Humidity']
hotel_df = ideal_weather_df[columns_to_copy].copy()

# Add an empty column, "Hotel Name," to the DataFrame so you can store the hotel found using the Geoapify API
hotel_df['Hotel Name'] = ''

# Display sample data
hotel_df

City Country      Lat       Lng  Humidity Hotel Name
83                champoton      MX  19.3500  -90.7167        81           
130                   crane      US  31.3974 -102.3501        73           
184             isla aguada      MX  18.7833  -91.4667        72           
195         lazaro cardenas      MX  17.9583 -102.2000        62           
203                galliano      US  29.4422  -90.2992        82           
220      brisas de zicatela      MX  15.8369  -97.0419        71           
234                celestun      MX  20.8667  -90.4000        75           
251             sellersburg      US  38.3981  -85.7550        48           
253         dzilam gonzalez      MX  21.2833  -88.9333        80           
257            san patricio      US  28.0170  -97.5169        85           
268                 cabanas      CU  22.9758  -82.9219        71           
277          cabo san lucas      MX  22.8909 -109.9124        91           
330                mazatlan      MX  23.2167 -106.4167        83           
349           bahia de kino      MX  28.8333 -111.9333        81           
434                robinson      US  31.4677  -97.1147        89           
523               ingleside      US  27.8778  -97.2117        88           
564                  panaba      MX  21.2833  -88.2667        79           
565  tlahualilo de zaragoza      MX  26.1167 -103.4500        14

### Step 4: For each city, use the Geoapify API to find the first hotel located within 10,000 metres of your coordinates.

In [65]:
# Dependencies and Setup
import hvplot.pandas
import pandas as pd
import requests

# Import API key
from api_keys import geoapify_key

# Set parameters to search for a hotel
# Define the latitude, longitude, and radius for the search
latitude = 31.3974  # Example latitude (New York)
longitude = -102.3501  # Example longitude (New York)
radius = 100000  # Example radius in meters (5 kilometers)
limit=20
params = {
    "categories":"accommodation.hotel",
    "apiKey": geoapify_key,
    "limit":limit,
    "filter": f"circle:{latitude},{longitude},{radius}",  
    # "bias": f"proximity:{latitude},{longitude}"          
}
base_url = "https://api.geoapify.com/v2/places"
name_address = requests.get(base_url, params=params)
name_address = name_address.json()
name_address


{'type': 'FeatureCollection', 'features': []}

In [6]:
# Set parameters to search for a hotel
radius = # YOUR CODE HERE
params = {
    # YOUR CODE HERE
}

# Print a message to follow up the hotel search
print("Starting hotel search")

# Iterate through the hotel_df DataFrame
for index, row in hotel_df.iterrows():
    # get latitude, longitude from the DataFrame
    # YOUR CODE HERE
    
    # Add filter and bias parameters with the current city's latitude and longitude to the params dictionary
    params["filter"] = # YOUR CODE HERE
    params["bias"] = # YOUR CODE HERE
    
    # Set base URL
    base_url = "https://api.geoapify.com/v2/places"


    # Make and API request using the params dictionaty
    name_address = # YOUR CODE HERE
    
    # Convert the API response to JSON format
    name_address = # YOUR CODE HERE
    
    # Grab the first hotel from the results and store the name in the hotel_df DataFrame
    try:
        hotel_df.loc[index, "Hotel Name"] = name_address["features"][0]["properties"]["name"]
    except (KeyError, IndexError):
        # If no hotel is found, set the hotel name as "No hotel found".
        hotel_df.loc[index, "Hotel Name"] = "No hotel found"
        
    # Log the search results
    print(f"{hotel_df.loc[index, 'City']} - nearest hotel: {hotel_df.loc[index, 'Hotel Name']}")

# Display sample data
hotel_df

Starting hotel search
kapaa - nearest hotel: Pono Kai Resort
hilo - nearest hotel: Dolphin Bay Hotel
banda - nearest hotel: #acnindiafy21
makakilo city - nearest hotel: Embassy Suites by Hilton Oahu Kapolei
kahului - nearest hotel: Maui Seaside Hotel
gat - nearest hotel: No hotel found
laguna - nearest hotel: Holiday Inn Express & Suites
tikaitnagar - nearest hotel: No hotel found
san quintin - nearest hotel: Jardines Hotel
santa rosalia - nearest hotel: Hotel del Real
narwar - nearest hotel: No hotel found
port hedland - nearest hotel: The Esplanade Hotel
roebourne - nearest hotel: No hotel found
saint-francois - nearest hotel: Chez Lily
capoterra - nearest hotel: Rosa Hotel
stolac - nearest hotel: Bregava
guerrero negro - nearest hotel: Plaza sal paraiso


City Country      Lat       Lng  Humidity  \
45            kapaa      US  22.0752 -159.3190        84   
51             hilo      US  19.7297 -155.0900        83   
63            banda      IN  25.4833   80.3333        52   
81    makakilo city      US  21.3469 -158.0858        81   
152         kahului      US  20.8947 -156.4700        60   
197             gat      IL  31.6100   34.7642       100   
211          laguna      US  38.4210 -121.4238        79   
240     tikaitnagar      IN  26.9500   81.5833        59   
265     san quintin      MX  30.4833 -115.9500        74   
340   santa rosalia      MX  27.3167 -112.2833        56   
363          narwar      IN  25.6500   77.9000        55   
375    port hedland      AU -20.3167  118.5667        73   
381       roebourne      AU -20.7833  117.1333        65   
391  saint-francois      FR  46.4154    3.9054        57   
409       capoterra      IT  39.1763    8.9718        71   
421          stolac      BA  43.0844   17.9575        68   
516  guerrero negro      MX  27.9769 -114.0611        68   

                                Hotel Name  
45                         Pono Kai Resort  
51                       Dolphin Bay Hotel  
63                           #acnindiafy21  
81   Embassy Suites by Hilton Oahu Kapolei  
152                     Maui Seaside Hotel  
197                         No hotel found  
211           Holiday Inn Express & Suites  
240                         No hotel found  
265                         Jardines Hotel  
340                         Hotel del Real  
363                         No hotel found  
375                    The Esplanade Hotel  
381                         No hotel found  
391                              Chez Lily  
409                             Rosa Hotel  
421                                Bregava  
516                      Plaza sal paraiso

### Step 5: Add the hotel name and the country as additional information in the hover message for each city in the map.

In [7]:
%%capture --no-display

# Configure the map plot
# YOUR CODE HERE

# Display the map
# YOUR CODE HERE

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Humidity,Hotel Name,Country)